## App ID Scraping
We're interested in knowing the app identifier (e.g. com.foobar.app) behind every application name mentioned in the dataset in order to reliably identify the app behind the transactions.

### Dataset Cleaning
We remove rows involving 'Play Points', we might consider them later.

In [1]:
import pandas as pd

df = pd.read_json('unique_game_ids.json')
df.columns = ['app_name']

# Drop rows that contain 'Play Points' in their names
df = df[~df['app_name'].str.contains('Play Points', na=False)]

### App Search
We search for the app on the Play Store using its name and then return the closest reasonable match if there is any.

### Match Functions
We need functions that define, given a set of results, the closest match

In [2]:
from google_play_scraper import search
from difflib import get_close_matches

# Too bad, apps often change their names
def get_first_app_id(app_name):
    results = search(app_name, lang="en", country="us")
    for result in results:
        if result['title'].lower() == app_name.lower():
            return result['appId']
    return None

# Uses fuzzy matching with a reasonable threshold, yields around 75% success rate!
def get_closest_app_id(app_name):
    try:
        results = search(app_name, lang="en", country="us")
        titles = [r['title'] for r in results]
        close_matches = get_close_matches(app_name, titles, n=1, cutoff=0.6)
        if close_matches:
            # Find the result that matches the best title
            match_title = close_matches[0]
            for result in results:
                if result['title'] == match_title:
                    return result['appId']
    except Exception as e:
        print(f"Error searching for {app_name}: {e}")
    return None

Loaded 495 SOCKS5 proxies from Mullvad.


#### Single-Threaded Search Version (it takes 2h for our 11000 app names...)

In [3]:
# Apply the fetch app ID function to each row
#from tqdm import tqdm
#tqdm.pandas()
#df['app_id'] = df['app_name'].progress_apply(get_closest_app_id)
#
## Compute ratio of successful matches
#total_apps = len(df)
#found_count = df['app_id'].notna().sum()
#success_ratio = found_count / total_apps
#
#print(f"Found {found_count} out of {total_apps} apps. Success ratio: {success_ratio:.2%}")

#### "Gotta Go Fast" Version (Google doesn't like it!! (But I use Mullvad to rotate proxies 😊🕳️🪏🤫))

##### Load Latest Mullvad Relays

In [4]:
import requests

# Ask Mullvad for its relays
answer = requests.get("https://api.mullvad.net/www/relays/all/")
relays = answer.json()
# Only keep the ones that work over SOCKS
proxies = [
    f"socks5h://{relay['ipv4_addr_in']}:1080"
    for relay in relays
    if relay.get('socks_name') and relay.get('ipv4_addr_in')
]

print(f"Loaded {len(proxies)} SOCKS5 proxies from Mullvad.")

Loaded 495 SOCKS5 proxies from Mullvad.


##### Inject Proxy Rotation Into The HTTP Get Function

In [5]:
import random
import functools
from google_play_scraper import search
from urllib.request import Request, urlopen, ProxyHandler, build_opener


# Backup the original function
original_urlopen = urlopen

# Define the proxy-rotating function
def proxied_urlopen(request, *args, **kwargs):
    proxy = random.choice(proxies)
    print('Rotating to proxy on '+proxy)
    proxy_handler = ProxyHandler({
        'http': proxy,
        'https': proxy,
    })
    opener = build_opener(proxy_handler)
    return opener.open(request, *args, **kwargs)

# Monkey-patch the HTTP GET request function with the proxy-rotating one
print(urlopen)
urlopen = proxied_urlopen
print(urlopen)

<function urlopen at 0x104c64680>
<function proxied_urlopen at 0x116983100>


##### Fetch App IDs in a Threaded Way

In [6]:

from concurrent.futures import ThreadPoolExecutor, as_completed
from difflib import get_close_matches
from tqdm import tqdm

# Use a tuple of (df_index, app_name)
def fetch_app_id_with_index(index, app_name):
    return index, get_closest_app_id(app_name)

def run_threaded_app_search(df, max_workers=10):
    results_dict = {}

    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        futures = {
            executor.submit(fetch_app_id_with_index, idx, row['app_name']): idx
            for idx, row in df.iterrows()
        }
        for future in tqdm(as_completed(futures), total=len(futures), desc="Searching apps"):
            idx, app_id = future.result()
            results_dict[idx] = app_id

    # Map results into a new column using original DataFrame index
    df['app_id'] = df.index.map(results_dict.get)
    return df

# Now run it safely
print(urlopen)
urlopen = proxied_urlopen
df = run_threaded_app_search(df)

<function proxied_urlopen at 0x116983100>
Using proxy: socks5h://gb-lon-wg-socks5-303.relays.mullvad.net:1080
Using proxy: socks5h://nl-ams-wg-socks5-004.relays.mullvad.net:1080
Using proxy: socks5h://us-chi-wg-socks5-305.relays.mullvad.net:1080
Using proxy: socks5h://gb-mnc-wg-socks5-002.relays.mullvad.net:1080
Using proxy: socks5h://us-lax-wg-socks5-606.relays.mullvad.net:1080
Using proxy: socks5h://se-mma-wg-socks5-012.relays.mullvad.net:1080
Using proxy: socks5h://se-got-wg-socks5-002.relays.mullvad.net:1080
Using proxy: socks5h://us-den-wg-socks5-205.relays.mullvad.net:1080
Using proxy: socks5h://ca-yyc-wg-socks5-202.relays.mullvad.net:1080
Using proxy: socks5h://us-chi-wg-socks5-308.relays.mullvad.net:1080


Searching apps:   0%|          | 3/10883 [00:06<5:29:49,  1.82s/it] 

Using proxy: socks5h://mx-qro-wg-socks5-004.relays.mullvad.net:1080
Using proxy: socks5h://cl-scl-wg-socks5-001.relays.mullvad.net:1080
Using proxy: socks5h://jp-tyo-wg-socks5-002.relays.mullvad.net:1080
Using proxy: socks5h://dk-cph-wg-socks5-401.relays.mullvad.net:1080
Using proxy: socks5h://it-mil-wg-socks5-003.relays.mullvad.net:1080


Searching apps:   0%|          | 6/10883 [00:07<2:23:22,  1.26it/s]

Using proxy: socks5h://us-lax-wg-socks5-409.relays.mullvad.net:1080
Using proxy: socks5h://fr-par-wg-socks5-001.relays.mullvad.net:1080
Using proxy: socks5h://pe-lim-wg-socks5-002.relays.mullvad.net:1080


...

Searching apps: 100%|█████████▉| 10879/10883 [23:13<00:00, 10.36it/s]

Using proxy: socks5h://se-mma-wg-socks5-102.relays.mullvad.net:1080


Searching apps: 100%|█████████▉| 10881/10883 [23:18<00:01,  1.44it/s]

Retrying in 5.8s due to: SOCKSHTTPSConnectionPool(host='play.google.com', port=443): Max retries exceeded with url: /store/search?q=Zombie%20Hive&c=apps&hl=en&gl=us (Caused by ConnectTimeoutError(<urllib3.contrib.socks.SOCKSHTTPSConnection object at 0x117d9e7b0>, 'Connection to play.google.com timed out. (connect timeout=10)'))
Retrying in 5.5s due to: SOCKSHTTPSConnectionPool(host='play.google.com', port=443): Max retries exceeded with url: /store/search?q=Zombieland%3A%20Doomsday%20Survival&c=apps&hl=en&gl=us (Caused by ConnectTimeoutError(<urllib3.contrib.socks.SOCKSHTTPSConnection object at 0x11765edb0>, 'Connection to play.google.com timed out. (connect timeout=10)'))
Using proxy: socks5h://nl-ams-wg-socks5-007.relays.mullvad.net:1080
Using proxy: socks5h://us-atl-wg-socks5-202.relays.mullvad.net:1080


Searching apps: 100%|██████████| 10883/10883 [23:27<00:00,  7.73it/s]


### Save Dataset

In [9]:
df.to_csv("OtherData/AppIdData/app_ids.csv", index=False)

### Reading The Saved Dataset

In [ ]:
df = pd.read_csv('OtherData/AppIdData/app_ids.csv')

# Compute ratio of successful matches
total_apps = len(df)
found_count = df['app_id'].notna().sum()
success_ratio = found_count / total_apps

print(f"Found {found_count} out of {total_apps} apps. Success ratio: {success_ratio:.2%}")

# Read in full
from IPython.display import display
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)       
pd.set_option('display.max_colwidth', None)
display(df) 

Found 8783 out of 10883 apps. Success ratio: 80.70%


app_name  \
0                                                                                     94%   
1                                                                                    2048   
2                                                                                  50,000   
3                                                                                  #DRIVE   
4                                                          #open Polyamorous Dating + ENM   
5                                                          ?°ã©?³ã?«ã¼?ã¡?³ã¿?¸ã¼   
6                                                               [Premium] RPG Chronus Arc   
7                                                    [root] AirAudio - stream your music!   
8                                                                         [root] CF.lumen   
9                                                                        [root] Servicely   
10                                                 [VIP]Missile Dude RPG: Tap Tap Missile   
11                                       0xUniverse: Conquer the blockchain-based galaxy!   
12                                                         1 2 3 4 Player Games - Offline   
13                                                                    10 Billion Husbands   
14                                                                       10 Billion Wives   
15                                                                       10 billion wives   
16                                                              10 Pin Shuffleâ¢ Bowling   
17                                                             100 DAYS - Zombie Survival   
18                                                         100 Doors - Escape from Prison   
19                                                                    100 Doors Challenge   
20                                                           100 PICS Quiz - FREE Quizzes   
21                                                             100 Years - Life Simulator   
22                                                                1010! Block Puzzle Game   
23                                                                           1010! Puzzle   
24                                                         10K Running: 0-5K-10K Training   
25                                                         150+ Solitaire Card Games Pack   
26                                                                                  1655F   
27                                                                                    17+   
28                                                                17TRACK Package Tracker   
29                                                         1945 Air Force: Airplane games   
30                                                                      1945 US Air Force   
31                                                              1998 Cam - Vintage Camera   
32                                                                            1-Bit Rogue   
33                                         1Password - Password Manager and Secure Wallet   
34                                                            1Password: Password Manager   
35                                     1Weather : Forecasts, Widgets, Snow Alerts & Radar   
36                                                             1Weather: Forecast & Radar   
37                                      1Weather: Forecasts, Widgets, Snow Alerts & Radar   
38                                                         1Weather:Widget Forecast Radar   
39                                                    2 For 2: Connect the Numbers Puzzle   
40                                                         2 Player games : the Challenge   
41                                                                       20 Billion Wives   
42                                                                  2048 Kitty Cat